In [1]:
import os
os.chdir('..')
print(os.getcwd())

/workspace/rendering


In [2]:
import plotly.graph_objects as go


def add_mesh(fig, mesh, **kwargs):
    # fig = go.Figure()
    x, y, z = mesh.vertices.T
    i, j, k = mesh.faces.T
    fig.add_trace(
        go.Mesh3d(x=x,y=y,z=z,i=i,j=j,k=k, **kwargs)
    )
    return fig

In [3]:
import torch
import trimesh
import numpy as np

def get_another_obj_mesh(anno, name):
    obj_filename = f'data/models/{name}/textured_simple.obj'
    obj_trimesh = trimesh.load_mesh(obj_filename)

    obj_verts = torch.tensor(obj_trimesh.vertices, dtype=torch.float32)
    obj_faces = torch.tensor(obj_trimesh.faces, dtype=torch.int64)
    obj_uv = torch.tensor(obj_trimesh.visual.uv, dtype=torch.float32)
    obj_map = torch.from_numpy(np.array(obj_trimesh.visual.material.image, dtype=np.float32)) / 255.0

    return obj_verts, obj_faces, obj_uv, obj_map

In [4]:
from utils.mano import ManoLayer
from utils.utils import load_ho_meta, get_obj_mesh, apply_transform_to_mesh
import trimesh


mano = ManoLayer()
anno = load_ho_meta("data/HO3D_v3/train/ABF10/meta/0000.pkl")

mano_hand = mano(anno)

obj_verts, obj_faces, obj_uv, obj_map = get_another_obj_mesh(anno, "025_mug")
obj_verts = apply_transform_to_mesh(obj_verts, anno)

handjoints = anno['handJoints3D']

# print(mano_hand.vertices.shape, mano.faces.shape)
mano_mesh = trimesh.Trimesh(vertices=mano_hand.vertices[0], faces=mano.faces, )
obj_mesh = trimesh.Trimesh(vertices=obj_verts, faces=obj_faces)
# scene = trimesh.Scene([mano_mesh, obj_mesh])
# lights, transforms = trimesh.scene.lighting.autolight(scene)

# scene.show()

/workspace/rendering/utils/utils.py:23: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  if v is None or v == 'None':


torch.Size([16762, 3]) torch.Size([3, 3]) torch.Size([3])


In [5]:
import numpy as np
import torch

def calc_face_normals(verts, faces):
    v1 = verts[faces[:,0].type(torch.long)]
    v2 = verts[faces[:,1].type(torch.long)]
    v3 = verts[faces[:,2].type(torch.long)]
    face_normals = np.cross(v2-v1, v3-v1)
    face_normals = face_normals / np.linalg.norm(face_normals, axis=1)[:,None]
    return face_normals

print(calc_face_normals(obj_verts, obj_faces))
print(obj_mesh.face_normals)

[[-0.35157177 -0.71106696 -0.608918  ]
 [-0.17475106 -0.34594697 -0.9218367 ]
 [-0.22923078 -0.38277364 -0.8949512 ]
 ...
 [ 0.02071286 -0.9406944   0.33862236]
 [-0.32099113 -0.9055417   0.2774148 ]
 [-0.06379485  0.9937164  -0.09196591]]
[[-0.35157174 -0.71106695 -0.60891798]
 [-0.17475106 -0.34594695 -0.92183663]
 [-0.22923077 -0.38277361 -0.89495118]
 ...
 [ 0.02071285 -0.94069436  0.33862235]
 [-0.32099106 -0.9055417   0.27741479]
 [-0.06379485  0.9937165  -0.09196592]]


In [6]:
def calc_vertex_normals(verts, faces):
    face_normals = calc_face_normals(verts, faces)
    vertex_normals = np.zeros(verts.shape)
    for i, face in enumerate(faces):
        vertex_normals[face] += face_normals[i]
    vertex_normals = vertex_normals / np.linalg.norm(vertex_normals, axis=1)[:,None]
    return vertex_normals

print(calc_vertex_normals(obj_verts, obj_faces))
print(obj_mesh.vertex_normals)

[[-0.17779046 -0.40907408 -0.89501338]
 [-0.15771536 -0.46583809 -0.87070129]
 [-0.22337506 -0.43685135 -0.87135784]
 ...
 [ 0.24244144 -0.74117404  0.62600574]
 [-0.51980363  0.40881211  0.75011789]
 [-0.12562009 -0.97319846  0.1926249 ]]
[[-0.19210834 -0.42282949 -0.88561256]
 [-0.20349705 -0.36262818 -0.90944475]
 [-0.16472718 -0.4476407  -0.87890998]
 ...
 [ 0.0476162  -0.94049586 -0.33645241]
 [ 0.14784522 -0.62094369  0.76978616]
 [-0.48055445 -0.54076391  0.69039251]]


In [11]:
class SinedDistanceNormals:
    def __init__(self):
        pass

    def calc_sd_normals(self, obj_mesh, handjoints):
        closest, distance, triangle_id = trimesh.proximity.closest_point(obj_mesh, handjoints)
        
        obj_verts = torch.tensor(obj_mesh.vertices)
        obj_faces = torch.tensor(obj_mesh.faces)
        face_normals = calc_face_normals(obj_verts, obj_faces)
        closest_normals = face_normals[triangle_id]
        sd_normals = closest_normals * distance[:,None]

        self.closest = closest
        self.distance = distance
        self.closest_normals = closest_normals
        self._sd_normals = sd_normals
        return sd_normals

sd = SinedDistanceNormals()
sd_normals = sd.calc_sd_normals(obj_mesh, handjoints)
print(sd.distance, sd.distance.shape)
print(sd_normals, sd_normals.shape)

[0.11878311 0.0395622  0.03471777 0.02811581 0.04259924 0.03953189
 0.04604252 0.07011279 0.05910511 0.05099802 0.05725685 0.042823
 0.03978862 0.08918057 0.0673103  0.04559963 0.02560477 0.0269872
 0.03695765 0.04022655 0.04534475] (21,)
[[-0.08822116  0.06791126  0.04140671]
 [-0.01329037  0.03181934  0.01939235]
 [ 0.0203841   0.02454689  0.01368438]
 [ 0.01537922  0.00387299  0.02321591]
 [-0.01574323  0.02180351  0.03303715]
 [ 0.03226248  0.00379125  0.02252841]
 [ 0.00601548  0.01101948  0.04429784]
 [-0.03900619  0.01307746  0.05677411]
 [-0.01464136  0.00277705  0.05719557]
 [ 0.00455954 -0.01064664  0.04966546]
 [-0.0238289   0.01909025  0.04843648]
 [-0.00648625  0.00410098  0.0421298 ]
 [ 0.00590197 -0.01046864  0.03793031]
 [-0.07808952  0.02968688  0.03120722]
 [-0.06106491  0.0279123   0.00475993]
 [-0.04493078 -0.0077789   0.00019967]
 [-0.01135687 -0.02267014  0.00356237]
 [ 0.01309336  0.00608303  0.02280065]
 [ 0.0147094   0.00918063  0.03263767]
 [ 0.00273676  0.002

In [8]:
fig = go.Figure()
add_mesh(fig, mano_mesh, opacity=1.0)
add_mesh(fig, obj_mesh, opacity=0.5)
fig.add_trace(go.Scatter3d(x=handjoints[:,0], y=handjoints[:,1], z=handjoints[:,2], mode='markers', marker=dict(size=5), name='handjoints'))
fig.add_trace(
    go.Scatter3d(
        x=sd.closest[:,0], 
        y=sd.closest[:,1], z=sd.closest[:,2], mode='markers', marker=dict(size=5)
        )
    )

for p1, p2 in zip(handjoints, sd.closest):
    fig.add_trace(
        go.Scatter3d(
            x=[p1[0], p2[0]], y=[p1[1], p2[1]], z=[p1[2], p2[2]], 
            mode='lines', line=dict(width=3, color='orange'),
            name='closest'
        )
        )

for p, n in zip(sd.closest, sd_normals):
    fig.add_trace(
        go.Scatter3d(
            x=[p[0], p[0]+n[0]], y=[p[1], p[1]+n[1]], z=[p[2], p[2]+n[2]], 
            mode='lines', line=dict(width=3, color='cyan'),
            name='sd_normals'
        )
        )

# fig.add_trace(
#     go.Cone(
#         x=closest[:,0], y=closest[:,1], z=closest[:,2], u=sd_normals[:,0], v=sd_normals[:,1], w=sd_normals[:,2], colorscale='Viridis', sizemode='scaled', sizeref=10
#     )
# )
fig.show()